# BMG Labtech CLARIOstar Plus

| Summary | Photo |
|---------|-------|
| <ul style="font-size:15px; line-height:1.6; margin-top:0;"> <li><a href="https://www.bmglabtech.com/en/clariostar-plus/" target="_blank"><b>OEM Link</b></a></li> <li><b>Communication Protocol / Hardware:</b> Serial (FTDI) / USB</li> <li><b>Communication Level:</b> Firmware</li> <li><b>Measurement Modes:</b> Absorbance (implemented), Fluorescence (planned), Luminescence (planned)</li> <li><b>Optical Systems:</b> Dual LVF Monochromator, Physical Filters, UV/Vis Spectrometer (220–1000 nm combined range)</li> <li><b>Plate Delivery:</b> Drawer</li> <li><b>Additional Features:</b> Temperature control, Shaking, Rapid full-plate autofocus, Configurable scan modes</li> <li>VID:PID <code>0403:BB68</code></li> </ul> | <div style="width:320px; text-align:center;"> ![clariostar](img/bmg-labtech-clariostar-plus.png) <br><i>Figure: BMG Labtech CLARIOstar Plus</i> </div> |

**CLARIOstar Plus vs CLARIOstar:** The CLARIOstar Plus (post-2019) replaced the original CLARIOstar. Both share the dual LVF Monochromator + filter + spectrometer architecture. The Plus adds rapid full-plate autofocus, newer PMT options (e.g. far-red), and Voyager control software. EDR (Enhanced Dynamic Range) was introduced after 2024 and is **not** present on all CLARIOstar Plus units. This backend targets the CLARIOstar Plus but may also work with the original CLARIOstar (untested).

---
## Setup Instructions (Physical)

The CLARIOstar and CLARIOstar Plus require a minimum of two cable connections to be operational:
1. Power cord (standard IEC C13)
2. USB cable (USB-B with security screws at CLARIOstar end; USB-A at control PC end)

Optional:
If you have a plate stacking unit to use with the CLARIOstar (Plus), an additional RS-232 port is available on the CLARIOstar (Plus).

---
## Setup Instructions (Programmatic)

To control the BMG Labtech CLARIOstar Plus, create a `PlateReader` frontend
instance that uses a `CLARIOstarPlusBackend` as its backend.

Currently supported: `setup()`, `open()`, `close()`, `stop()`, status polling,
device identification (EEPROM, firmware, usage counters), temperature control,
and absorbance measurement (discrete wavelengths).
Fluorescence and luminescence will be added in later phases.

In [1]:
import logging
import os
import time

from pylabrobot import verbose

verbose(True)

# Write a DEBUG-level trace log so every sent/received frame is captured.
# Uses .txt extension because .log is in .gitignore.
# If the existing log is older than 60 s it belongs to a previous run — start
# a fresh file.  Otherwise append so re-running this cell mid-session doesn't
# discard data.
_log_path = "clariostar_trace.txt"
_mode = "a"
if os.path.exists(_log_path):
    age = time.time() - os.path.getmtime(_log_path)
    if age > 60:
        _mode = "w"
else:
    _mode = "w"

_plr_logger = logging.getLogger("pylabrobot")
_plr_logger.setLevel(logging.DEBUG)
_fh = logging.FileHandler(_log_path, mode=_mode)
_fh.setLevel(logging.DEBUG)
_fh.setFormatter(logging.Formatter("%(asctime)s %(levelname)s %(message)s"))
_plr_logger.addHandler(_fh)
print(f"Trace log: {_log_path} ({'new file' if _mode == 'w' else 'appending'})")

Trace log: clariostar_trace.txt (new file)


In [2]:
from pylabrobot.plate_reading import PlateReader
from pylabrobot.plate_reading.bmg_labtech import CLARIOstarPlusBackend

clariostar_plus_backend = CLARIOstarPlusBackend()

pr = PlateReader(
    name="CLARIOstar",
    backend=clariostar_plus_backend,
    size_x=0.0,
    size_y=0.0,
    size_z=0.0,
)

If you have multiple FTDI devices connected, pass a `device_id` to the backend to select the correct one:

```python
clariostar_plus_backend = CLARIOstarPlusBackend(device_id="FT1234AB")
```

In [3]:
await pr.setup()

2026-02-26 18:14:44,922 - pylabrobot.io.ftdi - INFO - Successfully opened FTDI device: 430-2621
2026-02-26 18:14:45,181 - pylabrobot - INFO - read 24 bytes: 0200180c011506260000030000000000f400fbe000033a0d
2026-02-26 18:14:45,219 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000f400fbe00003270d
2026-02-26 18:14:45,220 - pylabrobot - INFO - status: {'standby': False, 'busy': False, 'running': False, 'valid': True, 'unread_data': False, 'lid_open': False, 'initialized': True, 'reading_wells': False, 'z_probed': True, 'plate_detected': True, 'drawer_open': False, 'filter_cover_open': False, 'temperature_bottom': 24.4, 'temperature_top': 25.1}
2026-02-26 18:14:45,259 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000f400fbe00003270d
2026-02-26 18:14:45,297 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000f400fbe00003270d
2026-02-26 18:14:45,371 - pylabrobot - INFO - read 271 bytes: 02010f0c070506260000000100000a0101010100000100ee02

```{note}
Expected behaviour: the machine performs its initialization routine (FTDI connection, baudrate configuration,
initialize command). The backend polls status until the device is no longer busy.
```

---
### Defining & Assigning a Plate

Every measurement requires a plate to be assigned to the plate reader (to tell the firmware what the positions for reading are).

In [4]:
from pylabrobot.resources.corning import Cor_96_wellplate_360ul_Fb

plate = Cor_96_wellplate_360ul_Fb("test_plate")
pr.assign_child_resource(plate)

---
## Usage: Drawer

The CLARIOstar loads and unloads plates via a motorized drawer.

In [5]:
# Open the drawer (plate out)
await pr.open()

2026-02-26 18:14:45,481 - pylabrobot - INFO - read 24 bytes: 0200180c012506260000030000000000f400fbe000034a0d
2026-02-26 18:14:45,523 - pylabrobot - INFO - read 24 bytes: 0200180c012506260000030000000000f400fbe000034a0d
2026-02-26 18:14:45,525 - pylabrobot - INFO - status: {'standby': False, 'busy': True, 'running': False, 'valid': True, 'unread_data': False, 'lid_open': False, 'initialized': True, 'reading_wells': False, 'z_probed': True, 'plate_detected': True, 'drawer_open': False, 'filter_cover_open': False, 'temperature_bottom': 24.4, 'temperature_top': 25.1}
2026-02-26 18:14:45,664 - pylabrobot - INFO - read 24 bytes: 0200180c012506260000030000000000f400fbe000034a0d
2026-02-26 18:14:45,665 - pylabrobot - INFO - status: {'standby': False, 'busy': True, 'running': False, 'valid': True, 'unread_data': False, 'lid_open': False, 'initialized': True, 'reading_wells': False, 'z_probed': True, 'plate_detected': True, 'drawer_open': False, 'filter_cover_open': False, 'temperature_bottom':

In [6]:
# Place your plate on the drawer (manually or via a robotic arm), then close it (plate in)
await pr.close()

2026-02-26 18:14:48,612 - pylabrobot - INFO - read 24 bytes: 0200180c012506210000030000000000f400fbe00003450d
2026-02-26 18:14:48,650 - pylabrobot - INFO - read 24 bytes: 0200180c012506210000030000000000f400fbe00003450d
2026-02-26 18:14:48,651 - pylabrobot - INFO - status: {'standby': False, 'busy': True, 'running': False, 'valid': True, 'unread_data': False, 'lid_open': False, 'initialized': True, 'reading_wells': False, 'z_probed': False, 'plate_detected': False, 'drawer_open': True, 'filter_cover_open': False, 'temperature_bottom': 24.4, 'temperature_top': 25.1}
2026-02-26 18:14:48,789 - pylabrobot - INFO - read 24 bytes: 0200180c012506210000030000000000f400fbe00003450d
2026-02-26 18:14:48,790 - pylabrobot - INFO - status: {'standby': False, 'busy': True, 'running': False, 'valid': True, 'unread_data': False, 'lid_open': False, 'initialized': True, 'reading_wells': False, 'z_probed': False, 'plate_detected': False, 'drawer_open': True, 'filter_cover_open': False, 'temperature_bottom

---
## Device Identification

EEPROM configuration, firmware info, usage counters, and status queries.

In [7]:
config = clariostar_plus_backend.configuration
for key, value in config.items():
    print(f"  {key:25s} {value}")

print()
modes = await clariostar_plus_backend.request_available_detection_modes()
print(f"  Available detection modes: {', '.join(modes) if modes else 'none'}")

2026-02-26 18:14:55,551 - pylabrobot - INFO - read 271 bytes: 02010f0c070506260000000100000a0101010100000100ee0200000f00e4030000000000000304000001000001020000000000000000000032000000000000000000000000000000000000000074006f0000000000000065000000dc050000000000000000f4010803a70408076009da08ac0d0000000000000000000000000000000000000000000000000100000001010000000000000001010000000000000012029806ae013d0a4605ee01fbff700c00000000a40058ff8e03f20460ff5511fe0b55118f1a170298065aff970668042603bc14b804080791009001463228460a0046071e00200398062003f2062103d40628002c01900146001e00001411001209ac0d60090000000000220c0d
2026-02-26 18:14:55,552 - pylabrobot - INFO - EEPROM: 263 bytes, head=070506260000000100000a0101010100


  serial_number             430-2621
  firmware_version          1.35
  firmware_build_timestamp  Nov 20 2020 11:51:21
  model_name                CLARIOstar Plus
  machine_type_code         1574
  max_temperature           45.0
  has_absorbance            True
  has_fluorescence          True
  has_luminescence          True
  has_alpha_technology      True
  excitation_monochromator_max_nm 750
  emission_monochromator_max_nm 996
  excitation_filter_slots   4
  dichroic_filter_slots     3
  emission_filter_slots     4

  Available detection modes: absorbance, absorbance_spectrum, fluorescence, luminescence, alpha_technology


In [8]:
counters = await clariostar_plus_backend.request_usage_counters()
for name, value in counters.items():
    print(f"  {name:25s} {value:>12,}")

2026-02-26 18:14:55,596 - pylabrobot - INFO - read 50 bytes: 0200320c210506260000001fe0330000081e0000056500000457000295bf000013d80000000a0000000a0000000a00050e0d


  flashes                      2,089,011
  testruns                         2,078
  wells                          138,100
  well_movements                 111,100
  active_time_s                  169,407
  shake_time_s                     5,080
  pump1_usage                         10
  pump2_usage                         10
  alpha_time                          10


In [9]:
status = await clariostar_plus_backend.request_machine_status()
for flag, value in status.items():
    print(f"  {flag:20s} {value}")

2026-02-26 18:14:55,644 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000f400fbe00003270d


  standby              False
  busy                 False
  running              False
  valid                True
  unread_data          False
  lid_open             False
  initialized          True
  reading_wells        False
  z_probed             True
  plate_detected       True
  drawer_open          False
  filter_cover_open    False
  temperature_bottom   24.4
  temperature_top      25.1


In [10]:
if await clariostar_plus_backend.sense_plate_present():
    print("Plate is in the drawer")
else:
    print("No plate detected")

if await clariostar_plus_backend.is_ready():
    print("Machine is ready")
else:
    print("Machine is busy")

2026-02-26 18:14:55,693 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000f400fbe00003270d
2026-02-26 18:14:55,734 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000f400fbe00003270d


Plate is in the drawer
Machine is ready


---
## Temperature

The CLARIOstar Plus has a dual-plate incubator (bottom + top heating elements) with
0.1 °C resolution. The firmware exposes three temperature modes via command family `0x06`:

| Mode | Payload | Effect |
|------|---------|--------|
| **OFF** | `0x0000` | Disable heating and sensor readout |
| **MONITOR** | `0x0001` | Activate sensors only (no heating) |
| **SET** | target x 10 | Heat to target °C and activate sensors |

```{important}
The firmware treats all three as a single-state register: each new `0x06` command
**replaces** the previous one. `measure_temperature()` is safe to call while heating
is active -- it internally activates monitoring in an idempotent way (checks if sensors
are already reporting and returns immediately if so), so it will never overwrite an
active heating setpoint.
```

### Reading the current temperature

`measure_temperature()` returns the current plate temperature. On the first call it
activates the sensors internally (~200 ms warmup); subsequent calls detect that sensors
are already reporting and return instantly.

In [11]:
temp = await clariostar_plus_backend.measure_temperature()
print(f"Temperature: {temp:.1f} °C")

target = clariostar_plus_backend.get_target_temperature()
print(f"Target temperature: {target}")  # None -- no heating active

2026-02-26 18:14:55,784 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000f400fbe00003270d
2026-02-26 18:14:55,825 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000f400fbe00003270d


Temperature: 24.4 °C
Target temperature: None


In [12]:
# Read each sensor individually, or the mean of both
bottom = await clariostar_plus_backend.measure_temperature(sensor="bottom")
top = await clariostar_plus_backend.measure_temperature(sensor="top")
mean = await clariostar_plus_backend.measure_temperature(sensor="mean")

print(f"Bottom plate: {bottom:.1f} °C")
print(f"Top plate:    {top:.1f} °C")
print(f"Mean:         {mean:.1f} °C")

2026-02-26 18:14:55,871 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000f400fbe00003270d
2026-02-26 18:14:55,910 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000f400fbe00003270d
2026-02-26 18:14:55,948 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000f400fbe00003270d
2026-02-26 18:14:55,986 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000f400fbe00003270d
2026-02-26 18:14:56,024 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000f400fbe00003270d
2026-02-26 18:14:56,062 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000f400fbe00003270d


Bottom plate: 24.4 °C
Top plate:    25.1 °C
Mean:         24.8 °C


### Checking temperature state

The CLARIOstar Plus firmware does not echo back the heating setpoint in its
status response, so pylabrobot tracks the target temperature on the host side.
`get_target_temperature()` returns the setpoint in °C, or `None` if no heating
is active. Because this is host-managed state (not queried from the device),
it uses `get_` nomenclature rather than `request_`.

In [13]:
target = clariostar_plus_backend.get_target_temperature()
print(f"Target temperature: {target}")  # None -- sensors active but no heating setpoint

Target temperature: None


### Heating to a target temperature

`start_temperature_control(target)` heats the incubator to the target °C.
Use `measure_temperature()` to monitor progress -- it is safe to call during
active heating (see note above).

`stop_temperature_control()` stops heating but keeps sensors active so
`measure_temperature()` continues to work without re-activating them.

In [14]:
import asyncio

# Before heating: no target set
print(f"Target temperature: {clariostar_plus_backend.get_target_temperature()}")  # None

# Start heating to 37 °C
await clariostar_plus_backend.start_temperature_control(37.0)
print(f"\nAfter start_temperature_control(37.0):")
print(f"Target temperature: {clariostar_plus_backend.get_target_temperature()}")  # 37.0

# Monitor until we reach the setpoint (or close enough)
for _ in range(5):
    temp = await clariostar_plus_backend.measure_temperature()
    print(f"Bottom plate: {temp:.1f} °C")
    if temp >= 36.5:
        print("Reached target range!")
        break
    await asyncio.sleep(2)

# Stop heating but keep sensors active
await clariostar_plus_backend.stop_temperature_control()
print(f"\nAfter stop_temperature_control():")
print(f"Target temperature: {clariostar_plus_backend.get_target_temperature()}")  # None

# Sensors still work after stopping heating
await asyncio.sleep(1)
temp = await clariostar_plus_backend.measure_temperature()
print(f"Bottom plate: {temp:.1f} °C")

2026-02-26 18:14:56,130 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000f400fbe00003270d
2026-02-26 18:14:56,168 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000f400fbe00003270d
2026-02-26 18:14:56,206 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000000000e00001380d


Target temperature: None


2026-02-26 18:14:56,544 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000f400fbe00003270d
2026-02-26 18:14:56,582 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000f400fbe00003270d



After start_temperature_control(37.0):
Target temperature: 37.0
Bottom plate: 24.4 °C


2026-02-26 18:14:58,620 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000f300fbe00003260d
2026-02-26 18:14:58,658 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000f300fbe00003260d


...

Bottom plate: 24.6 °C


2026-02-26 18:15:06,930 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000000000e00001380d



After stop_temperature_control():
Target temperature: None


2026-02-26 18:15:08,269 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000fa0103e00002360d
2026-02-26 18:15:08,307 - pylabrobot - INFO - read 24 bytes: 0200180c010506260000000000000000fa0103e00002360d


Bottom plate: 25.0 °C


---
## Absorbance

Single-wavelength and multi-wavelength discrete absorbance measurements with configurable
optics, scan direction, and shaking.

### Single wavelength

In [15]:
results = await pr.read_absorbance(
    wavelength=600,
    use_new_return_type=True,
)

print(f"OD at 600nm, well A1: {results[0]['data'][0][0]}")

2026-02-26 18:15:08,410 - pylabrobot - INFO - read 53 bytes: 0200350c032504260000000004bc0000018c010000003000000001010000000000000002000000260001000000020000ca00030a0d
2026-02-26 18:15:10,414 - pylabrobot - WARNING - data poll: bad frame (Response too short (0 bytes)), retrying
2026-02-26 18:15:10,468 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000fb0103e000033a0d
2026-02-26 18:15:10,472 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:15:11,511 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400fc0104e00002600d
2026-02-26 18:15:11,550 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000fc0104e000033c0d
2026-02-26 18:15:11,552 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:15:11,589 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400fc0104e00002600d
2026-02-26 18:15:11,632 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000fc0104e000033c0d
2026-02-26 18:15:11,634 - p

OD at 600nm, well A1: 3.6396003992870916


In [16]:
import pandas as pd

pd.DataFrame(results[0]["data"])

0         1         2         3         4         5         6   \
0  3.639600  3.553550  0.075142  1.153149  2.117829  2.889397  3.076622   
1  0.077308  3.674462  3.193378  3.341871  3.346049  3.562757  3.125764   
2  0.124747  0.123600  0.096641  0.087161  0.101558  0.118254  0.123401   
3  0.125781  0.126254  0.136912  0.170769  0.167490  0.187871  0.121560   
4  0.081441  0.078127  0.084155  0.075772  0.076328  0.073439  0.074085   
5  0.082189  0.076050  0.084944  0.081306  0.084051  0.081533  0.076384   
6  3.065763  3.049836  3.125810  3.099425  3.072906  3.126283  3.106618   
7  3.033710  3.072183  3.047390  3.108966  3.109205  3.074455  3.095680   

         7         8         9         10        11  
0  3.129214  3.032883  3.122164  0.121719  0.070729  
1  3.144956  2.921379  2.792725  0.117148  0.071774  
2  0.123389  2.348629  2.260098  0.101015  0.073627  
3  0.129920  1.640751  1.601164  0.098362  0.075316  
4  0.071747  0.841846  0.878453  0.085995  0.071827  
5  0.087755  0.125947  0.080272  0.083617  0.077652  
6  3.077740  3.051037  3.053596  3.097113  3.096415  
7  3.073780  3.121015  3.115550  3.118042  3.096156

### Output format: `report`

`read_absorbance` supports three output formats via the `report` parameter:

| `report=` | Output | Description |
|-----------|--------|-------------|
| `"optical_density"` (default) | OD values | `OD = -log10(T)` where `T = (sample / c_hi) × (r_hi / ref)` |
| `"transmittance"` | Percent transmittance | `T% = T × 100` |
| `"raw"` | Raw detector counts | Unprocessed counts + calibration metadata |

The raw mode is useful for debugging, custom calibration, or when you need access to the
underlying detector values and reference channel data.

In [17]:
# Optical density (default)
od_results = await pr.read_absorbance(wavelength=600, report="optical_density",
                                      use_new_return_type=True)
print(f"OD:            {od_results[0]['data'][0][0]:.4f}")

# Percent transmittance
trans_results = await pr.read_absorbance(wavelength=600, report="transmittance",
                                         use_new_return_type=True)
print(f"Transmittance: {trans_results[0]['data'][0][0]:.2f} %")

# Raw detector counts (includes calibration metadata)
raw_results = await pr.read_absorbance(wavelength=600, report="raw",
                                       use_new_return_type=True)
print(f"Raw counts:    {raw_results[0]['data'][0][0]:.0f}")
print(f"Chromatic cal: {raw_results[0]['chromatic_cal']}")
print(f"Reference cal: {raw_results[0]['reference_cal']}")

2026-02-26 18:15:49,577 - pylabrobot - INFO - read 53 bytes: 0200350c032504260000000004bc0000018c010000003000000001010000000000000002000000260001000000020000ca00030a0d
2026-02-26 18:15:51,582 - pylabrobot - WARNING - data poll: bad frame (Response too short (0 bytes)), retrying
2026-02-26 18:15:51,646 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000fd0103e000033c0d
2026-02-26 18:15:51,647 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:15:52,686 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400fd0103e00002600d
2026-02-26 18:15:52,724 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000fd0103e000033c0d
2026-02-26 18:15:52,726 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:15:52,766 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400fd0103e00002600d
2026-02-26 18:15:52,807 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000fd0103e000033c0d
2026-02-26 18:15:52,809 - p

OD:            3.6385


2026-02-26 18:16:33,468 - pylabrobot - WARNING - data poll: bad frame (Response too short (0 bytes)), retrying
2026-02-26 18:16:33,532 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000fc0103e000033b0d
2026-02-26 18:16:33,533 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:16:34,572 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400fb0103e000025e0d
2026-02-26 18:16:34,610 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000fb0103e000033a0d
2026-02-26 18:16:34,610 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:16:34,648 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400fb0103e000025e0d
2026-02-26 18:16:34,686 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000fb0103e000033a0d
2026-02-26 18:16:34,687 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:16:34,724 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400fb0103e000025e0d
2026-02-26 18

Transmittance: 0.03 %


2026-02-26 18:17:14,421 - pylabrobot - WARNING - data poll: bad frame (Response too short (0 bytes)), retrying
2026-02-26 18:17:14,487 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000fb0102e00003390d
2026-02-26 18:17:14,488 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:17:15,528 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400fb0102e000025d0d
2026-02-26 18:17:15,568 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000fb0102e00003390d
2026-02-26 18:17:15,569 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:17:15,606 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400fb0102e000025d0d
2026-02-26 18:17:15,644 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000fb0102e00003390d
2026-02-26 18:17:15,645 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:17:15,682 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400fb0102e000025d0d
2026-02-26 18

Raw counts:    2056
Chromatic cal: (7758313, 65744)
Reference cal: (36250, 0)


### Multi-wavelength

Pass a list of up to 8 discrete wavelengths. The firmware measures all wavelengths in a
single plate pass — each well is illuminated once per wavelength before the optic head
moves to the next well. Results are returned as a list of dicts, one per wavelength.

Each wavelength uses its own calibration pair for the OD calculation, so accuracy is
maintained across the full wavelength range.

In [18]:
results = await pr.read_absorbance(
    wavelength=260,
    wavelengths=[260, 280, 450, 600, 750],
    use_new_return_type=True,
)

for r in results:
    print(f"Wavelength {r['wavelength']} nm -> A1 OD: {r['data'][0][0]:.4f}")

2026-02-26 18:17:53,309 - pylabrobot - INFO - read 53 bytes: 0200350c0325042600000000026100000314010000003000000001010000000000000002000000260001000000020000ca0002370d
2026-02-26 18:17:55,314 - pylabrobot - WARNING - data poll: bad frame (Response too short (0 bytes)), retrying
2026-02-26 18:17:55,377 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000fa0101e00003370d
2026-02-26 18:17:55,378 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:17:56,417 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400fa0101e000025b0d
2026-02-26 18:17:56,456 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000fa0101e00003370d
2026-02-26 18:17:56,457 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:17:56,493 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400fa0101e000025b0d
2026-02-26 18:17:56,531 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000fa0101e00003370d
2026-02-26 18:17:56,532 - p

Wavelength 260 nm -> A1 OD: 3.5792
Wavelength 280 nm -> A1 OD: 3.5344
Wavelength 450 nm -> A1 OD: 0.1696
Wavelength 600 nm -> A1 OD: 3.8005
Wavelength 750 nm -> A1 OD: 0.0802


### Partial well selection

In [19]:
column_1_wells = [plate.get_item(f"{row}1") for row in "ABCDEFGH"]

results = await pr.read_absorbance(
    wavelength=600,
    wells=column_1_wells,
    use_new_return_type=True,
)

2026-02-26 18:18:34,665 - pylabrobot - INFO - read 53 bytes: 0200350c03250426000000002a9d0000002c010000000f000000010100000000000000020000000500010000000200003c0001e00d
2026-02-26 18:18:36,675 - pylabrobot - WARNING - data poll: bad frame (Response too short (0 bytes)), retrying
2026-02-26 18:18:36,730 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000fa0101e00003370d
2026-02-26 18:18:36,731 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:18:37,768 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400fa0101e000025b0d
2026-02-26 18:18:37,806 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000fa0101e00003370d
2026-02-26 18:18:37,807 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:18:37,844 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400fa0101e000025b0d
2026-02-26 18:18:37,882 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000fa0101e00003370d
2026-02-26 18:18:37,883 - p

### Optics: flashes and well scan mode

`flashes` controls how many flashes the light source fires per well (higher = lower noise,
slower measurement). The allowed range depends on `well_scan` mode:

| `well_scan=` | Flashes | Description | Useful for |
|---|---|---|---|
| `"point"` (default) | 1–200 | Single measurement at well centre | Fast screening |
| `"orbital"` | 1–44 | Average of points on a circular path | Reduce meniscus effects |
| `"spiral"` | 1–127 | Average of points on a spiral path | Dense/turbid samples |
| `"matrix"` | 1–200 | Grid of points (2×2 to 30×30) | Not yet implemented |

`scan_diameter_mm` sets the scan circle/spiral diameter (1–6 mm, ignored for `"point"`).


In [20]:
# Orbital scan with 7 flashes and 3 mm diameter
results = await pr.read_absorbance(
    wavelength=600,
    flashes=7,
    well_scan="orbital",
    scan_diameter_mm=3,
    use_new_return_type=True,
)

print(f"OD at 600nm (orbital), well A1: {results[0]['data'][0][0]:.4f}")

2026-02-26 18:18:42,834 - pylabrobot - INFO - read 53 bytes: 0200350c032504260000000004bc0000018c010000005000000001010000000000000005000000460001000000050000540002da0d
2026-02-26 18:18:44,841 - pylabrobot - WARNING - data poll: bad frame (Response too short (0 bytes)), retrying
2026-02-26 18:18:44,899 - pylabrobot - INFO - read 24 bytes: 0200180c01b504260000d50000000000f90101e00003b60d
2026-02-26 18:18:44,899 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:18:45,939 - pylabrobot - INFO - read 24 bytes: 0200180c01a504260000fa0500000000f90101e00003d00d
2026-02-26 18:18:45,977 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f90101e00003360d
2026-02-26 18:18:45,978 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:18:46,015 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f90101e000025a0d
2026-02-26 18:18:46,053 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f90101e00003360d
2026-02-26 18:18:46,053 - p

OD at 600nm (orbital), well A1: 2.6765


### Scan direction

Three parameters control the order in which the optic head visits wells:

| Parameter | Values | Default | Effect |
|---|---|---|---|
| `vertical` | `True` / `False` | `True` | `True` = column-major (A1→H1→A2…), `False` = row-major (A1→A12→B1…) |
| `unidirectional` | `True` / `False` | `True` | `True` = same direction each pass, `False` = serpentine (bidirectional) |
| `corner` | `"TL"` `"TR"` `"BL"` `"BR"` | `"TL"` | Starting corner of the scan path |

The defaults (`vertical=True`, `unidirectional=True`, `corner="TL"`) match the CLARIOstar
factory preset and are appropriate for most assays. Changing the direction or starting corner
can be useful for kinetic measurements where read order matters.

In [21]:
# Horizontal serpentine scan starting from bottom-right
results = await pr.read_absorbance(
    wavelength=600,
    vertical=False,
    unidirectional=False,
    corner="BR",
    use_new_return_type=True,
)

2026-02-26 18:19:55,261 - pylabrobot - INFO - read 53 bytes: 0200350c032504260000000004bc0000018c010000002e00000001010000000000000002000000240001000000020000d200030e0d
2026-02-26 18:19:57,267 - pylabrobot - WARNING - data poll: bad frame (Response too short (0 bytes)), retrying
2026-02-26 18:19:57,330 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f90100e00003350d
2026-02-26 18:19:57,332 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:19:58,370 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f90100e00002590d
2026-02-26 18:19:58,408 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f90100e00003350d
2026-02-26 18:19:58,409 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:19:58,448 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f90100e00002590d
2026-02-26 18:19:58,486 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f90100e00003350d
2026-02-26 18:19:58,492 - p

### Shaking

The CLARIOstar can shake the plate before reading to resuspend settled particles or
mix reagents. When `shake_mode` is set, all three shake parameters are **required**
to prevent silent misconfiguration (e.g. forgetting `shake_speed_rpm` and getting no shake):

| Parameter | Type | Description |
|---|---|---|
| `shake_mode` | `str` or `None` | `None` = no shake, `"orbital"`, `"double_orbital"`, or `"linear"` |
| `shake_speed_rpm` | `int` | Shake speed in RPM (multiples of 100, 100-700). Required when `shake_mode` is set. |
| `shake_duration_s` | `int` | Duration of shaking in seconds (> 0). Required when `shake_mode` is set. |
| `settling_time_s` | `float` | Wait time after shaking before reading (0.0-1.0 s). Required when `shake_mode` is set. |

```{important}
When `shake_mode` is `None` (default), the shake parameters must also be `None`.
When `shake_mode` is set, you must explicitly provide `shake_speed_rpm`,
`shake_duration_s`, and `settling_time_s` — there are no implicit defaults.
```


In [22]:
# Orbital shake at 300 RPM for 5 seconds, no settling delay before reading
results = await pr.read_absorbance(
    wavelength=600,
    well_scan="orbital",
    scan_diameter_mm=3,
    flashes=7,
    shake_mode="orbital",
    shake_speed_rpm=300,
    shake_duration_s=5,
    settling_time_s=0,
    use_new_return_type=True,
)

2026-02-26 18:20:35,009 - pylabrobot - INFO - read 53 bytes: 0200350c032504260000000004bc0000018c0100000059000000010100000000000000050000004f00010000000500004c0002e40d
2026-02-26 18:20:37,015 - pylabrobot - WARNING - data poll: bad frame (Response too short (0 bytes)), retrying
2026-02-26 18:20:37,078 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f90100e00003350d
2026-02-26 18:20:37,079 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:20:38,118 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f90100e00002590d
2026-02-26 18:20:38,156 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f90100e00003350d
2026-02-26 18:20:38,157 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:20:38,194 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f90100e00002590d
2026-02-26 18:20:38,232 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f90100e00003350d
2026-02-26 18:20:38,233 - p

### Non-blocking measurement (`wait=False`)

By default, `read_absorbance` polls the device incrementally until the measurement
is complete (`wait=True`). Setting `wait=False` fires the measurement and returns
an empty list immediately, letting you retrieve the data later with
`request_absorbance_results()`.

**Why two modes?**

| | Blocking (`wait=True`) | Non-blocking (`wait=False`) |
|---|---|---|
| **Control flow** | Awaits until data is ready | Returns immediately |
| **Best for** | Simple scripts, sequential workflows | Multi-instrument orchestration |
| **Throughput** | Plate reader sits idle between calls | Overlap measurement with other work |

In a typical lab automation workflow the plate reader measurement takes 10-30 seconds.
With blocking mode, the entire program waits. With non-blocking mode, that time can be
used to drive a liquid handler, move plates, or start measurements on other instruments
-- the same pattern as `asyncio` tasks but at the instrument level. This is especially
valuable in high-throughput screening where plate reader time is often the bottleneck.


In [23]:
# Fire-and-forget: start measurement, return immediately (empty list)
await pr.read_absorbance(wavelength=600, wait=False, use_new_return_type=True)

# ... do other work while the plate reader is measuring ...

# Check status until the device is no longer busy
status = await clariostar_plus_backend.request_machine_status()
while status["busy"]:
    print(f"Measuring... busy={status['busy']}")
    await asyncio.sleep(1)
    status = await clariostar_plus_backend.request_machine_status()

# Retrieve and parse the completed measurement (backend returns list of dicts directly)
results = await clariostar_plus_backend.request_absorbance_results(
    plate, plate.get_all_items(), [600]
)

print(f"OD at 600nm, well A1: {results[0]['data'][0][0]:.4f}")


2026-02-26 18:21:55,476 - pylabrobot - INFO - read 53 bytes: 0200350c032504260000000004bc0000018c010000003000000001010000000000000002000000260001000000020000ca00030a0d
2026-02-26 18:21:56,531 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f80100e00002580d


Measuring... busy=True


2026-02-26 18:21:57,587 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f80100e00002580d


Measuring... busy=True


2026-02-26 18:21:58,626 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f80100e00002580d


...

Measuring... busy=True


2026-02-26 18:22:34,983 - pylabrobot - INFO - read 24 bytes: 0200180c0125042e0000040100000300f80100e000025f0d


Measuring... busy=True


2026-02-26 18:22:36,022 - pylabrobot - INFO - read 24 bytes: 0200180c010507260000000000000000f80100e00002320d
2026-02-26 18:22:36,244 - pylabrobot - INFO - read 1612 bytes: 02064c0c020506260000a901880188001dffe20220030001006001000100000001010000000000f800000b0400000d2e00340c2700085adb0000eb3700002d7500001a5700001e8500001c3d0000181f0059d2700064d92d0063adf800000b1500001538000011c800000a9700000ca700001edb00001a2b000024eb00003327005adff30064bb2c00596419005975a9005f1bda006143e7005e04db005abba70059894e0059d7f2000091cb0000aed3005e3d960064b43b00592d1c00591a1c005689a60051534d0050d2b6004d57f60059fc31005853110002c4fc00030117005ee0440064407b00623c6c006398bc006268070063d6e40063cd8300649e1e006496db0064df830011652c000fc8de0061da010064d0430061d87f0063ecc20061ec430062d5820061e4e30061daab0063eebe0061edd6005918bc0062fd1a0061ab760063425000001ef000001c8700001b8f00001ace00001c1b00001df700001c9800001c4600001b4800001b3600001fa40000157200001e5d00001ec000001d5500001ad8000019bc00001ece00001e8100001b8800001d48000

OD at 600nm, well A1: 3.4415


---
### Measurement Timing Reference

Empirical timing data measured from USB packet captures on a CLARIOstar Plus
(firmware v1.35) with a 96-well Corning plate. All measurements
include ~4.5 s fixed overhead (drawer close + plate positioning).

#### Effect of well scan mode (96 wells, 600 nm)

| Scan mode | Flashes | Data phase | Total time | ms/well |
|-----------|---------|------------|------------|---------|
| Point     | 1       | 16.3 s     | ~21 s      | 170     |
| Point     | 5       | 31.4 s     | ~36 s      | 327     |
| Point     | 20      | 34.6 s     | ~39 s      | 360     |
| Orbital 3 mm | 5    | 56.7 s     | ~62 s      | 591     |
| Orbital 3 mm | 7    | 67.5 s     | ~73 s      | 703     |
| Orbital 5 mm | 7    | 79.6 s     | ~85 s      | 829     |
| Spiral 3 mm  | 15   | 82.1 s     | ~87 s      | 855     |
| Spiral 4 mm  | 15   | 115.7 s    | ~121 s     | 1205    |

**Key insight — flash marginal cost is tiny:** going from 1 to 5 flashes nearly
doubles the time, but 5 to 20 flashes barely changes it (31.4 s to 34.6 s). The
instrument fires all flashes in rapid succession at each well position, so most
of the time is spent on mechanical travel between wells, not flashing.

#### Effect of wavelength count (96 wells, point scan, 1 flash)

| Wavelengths | Data phase | ms/well |
|-------------|------------|---------|
| 1 (450 nm)            | 16.25 s | 169 |
| 2 (450 + 600 nm)      | 16.22 s | 169 |
| 3 (450 + 600 + 660 nm)| 16.27 s | 169 |

**Multiple wavelengths are free:** all wavelengths are measured simultaneously in
a single pass. The data phase is identical regardless of wavelength count.

#### Effect of well count (point scan, 5 flashes)

| Wells | Data phase | ms/well |
|-------|------------|---------|
| 1     | 0.8 s      | 792     |
| 8     | 2.9 s      | 362     |
| 48    | 15.8 s     | 329     |
| 96    | 31.4 s     | 327     |

The ms/well rate converges at ~327 ms for large well counts. The high per-well
cost at low counts reflects fixed overhead within the measurement cycle.

#### Effect of traversal order (96 wells, point scan, 1 flash)

| Direction | Data phase | ms/well |
|-----------|------------|---------|
| Horizontal serpentine   | 16.0 s | 167 |
| Bidirectional vertical  | 16.2–17.3 s | 169–180 |
| Unidirectional vertical | 21.1 s | 220 |

**Unidirectional is ~30% slower** than serpentine because the optic head must
return to the start of each column instead of reversing direction.

#### Effect of shaking (96 wells, orbital 3 mm, 7 flashes)

| Configuration | Shake phase | Data phase | Total |
|---------------|-------------|------------|-------|
| No shake      | —           | 67.5 s     | 72.6 s |
| Orbital 300 rpm / 5 s  | 7.3 s | 65.1 s | 78.4 s |
| Orbital 500 rpm / 5 s  | 7.3 s | 64.0 s | 77.3 s |
| Orbital 300 rpm / 10 s | 12.1 s | 63.5 s | 82.6 s |
| Linear 300 rpm / 5 s   | 7.4 s | 63.9 s | 77.3 s |

Shaking adds a clean pre-measurement phase (~2.3 s ramp overhead beyond the
configured duration) but does not affect the measurement itself.

```{note}
**Manual spec comparison:** The operating manual (0430B0006B, p.4) states
read times of 8 s (96-well), 15 s (384-well), and 28 s (1536-well) at 1 flash.
Our measured data phase for 96 wells at 1 flash is ~16.3 s — roughly double the
spec. The manual likely quotes the raw flash time excluding data transfer overhead,
or refers to an optimised firmware mode. All timings here include full USB data
retrieval as experienced by the calling program.
```

---
## Hardware Validation Tests

Systematic tests for every absorbance parameter. Run these cells on a physical
CLARIOstar Plus with a plate loaded to verify correct firmware communication.
Each cell prints a PASS/FAIL summary based on return shape and value sanity.

In [24]:
import json as _json
import traceback, time
from datetime import datetime, timezone
from tqdm.notebook import tqdm

# Accumulated test results — saved to JSON after all tests complete.
_all_results = {}
_test_run_start = datetime.now(timezone.utc).isoformat()

def _v(results, label, *, n_wl=1, n_wells=96, expect_cal=False):
    """Validate read_absorbance results: shape, types, optional cal keys."""
    try:
        assert isinstance(results, list), f"expected list, got {type(results)}"
        assert len(results) == n_wl, f"expected {n_wl} dicts, got {len(results)}"
        for r in results:
            assert "data" in r and "wavelength" in r, f"missing keys: {list(r.keys())}"
            flat = [v for row in r["data"] for v in row if v is not None]
            assert len(flat) == n_wells, f"expected {n_wells} measured values, got {len(flat)}"
            for v in flat:
                assert isinstance(v, (int, float)), f"non-numeric: {v}"
            if expect_cal:
                assert "chromatic_cal" in r and "reference_cal" in r
        print(f"  PASS  {label}")
        return True
    except Exception:
        print(f"  FAIL  {label}")
        traceback.print_exc()
        return False

async def _abs(label, n_wl=1, n_wells=96, expect_cal=False, **kw):
    """Run read_absorbance with given kwargs, validate, save results, return results."""
    kw.setdefault("wavelength", 600)
    kw["use_new_return_type"] = True
    _plr_logger.info("--- %s ---", label)
    t0 = time.monotonic()
    r = await pr.read_absorbance(**kw)
    dt = time.monotonic() - t0
    passed = _v(r, f"{label} ({dt:.1f}s)", n_wl=n_wl, n_wells=n_wells, expect_cal=expect_cal)
    _all_results[label] = {
        "passed": passed,
        "duration_s": round(dt, 2),
        "n_wl": n_wl,
        "n_wells": n_wells,
        "params": {k: v for k, v in kw.items() if k != "use_new_return_type"},
        "results": r,
    }
    return r

In [25]:
### T1: Well scan modes — point vs orbital vs spiral, varying diameters
print("=== T1: Well scan modes ===")
_t1_tests = [
    ("T1a point",       dict(well_scan="point")),
    ("T1b orbital 3mm", dict(well_scan="orbital", scan_diameter_mm=3, flashes=7)),
    ("T1c orbital 5mm", dict(well_scan="orbital", scan_diameter_mm=5, flashes=7)),
    ("T1d spiral 3mm",  dict(well_scan="spiral",  scan_diameter_mm=3, flashes=15)),
    ("T1e spiral 4mm",  dict(well_scan="spiral",  scan_diameter_mm=4, flashes=15)),
]
for label, kw in tqdm(_t1_tests, desc="T1"):
    await _abs(label, **kw)

=== T1: Well scan modes ===


T1:   0%|          | 0/5 [00:00<?, ?it/s]

2026-02-26 18:22:36,567 - pylabrobot - INFO - --- T1a point ---
2026-02-26 18:22:36,667 - pylabrobot - INFO - read 53 bytes: 0200350c032504260000000004bc0000018c010000003000000001010000000000000002000000260001000000020000ca00030a0d
2026-02-26 18:22:38,673 - pylabrobot - WARNING - data poll: bad frame (Response too short (0 bytes)), retrying
2026-02-26 18:22:38,734 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f80100e00003340d
2026-02-26 18:22:38,735 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:22:39,774 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f80100e00002580d
2026-02-26 18:22:39,812 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f80100e00003340d
2026-02-26 18:22:39,813 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:22:39,850 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f80100e00002580d
2026-02-26 18:22:39,888 - pylabrobot - INFO - read 24 bytes: 0200180c0135

  PASS  T1a point (40.9s)


2026-02-26 18:23:19,595 - pylabrobot - WARNING - data poll: bad frame (Response too short (0 bytes)), retrying
2026-02-26 18:23:19,658 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f800ffe00004320d
2026-02-26 18:23:19,659 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:23:20,698 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f800ffe00003560d
2026-02-26 18:23:20,736 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f800ffe00004320d
2026-02-26 18:23:20,737 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:23:20,774 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f800ffe00003560d
2026-02-26 18:23:20,812 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f800ffe00004320d
2026-02-26 18:23:20,813 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:23:20,850 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f800ffe00003560d
2026-02-26 18

...

  PASS  T1c orbital 5mm (95.5s)


2026-02-26 18:26:07,434 - pylabrobot - WARNING - data poll: bad frame (Response too short (0 bytes)), retrying
2026-02-26 18:26:07,495 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f600fee000042f0d
2026-02-26 18:26:07,496 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:26:08,537 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f600fee00003530d
2026-02-26 18:26:08,575 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f600fee000042f0d
2026-02-26 18:26:08,576 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:26:08,613 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f600fee00003530d
2026-02-26 18:26:08,653 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f600fee000042f0d
2026-02-26 18:26:08,655 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:26:08,691 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f600fee00003530d
2026-02-26 18

  PASS  T1d spiral 3mm (94.6s)


2026-02-26 18:27:42,057 - pylabrobot - WARNING - data poll: bad frame (Response too short (0 bytes)), retrying
2026-02-26 18:27:42,118 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f600fee000042f0d
2026-02-26 18:27:42,119 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:27:43,160 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f600fee00003530d
2026-02-26 18:27:43,200 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f600fee000042f0d
2026-02-26 18:27:43,202 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:27:43,240 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f600fee00003530d
2026-02-26 18:27:43,280 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f600fee000042f0d
2026-02-26 18:27:43,281 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:27:43,318 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f600fee00003530d
2026-02-26 18

  PASS  T1e spiral 4mm (128.1s)


In [30]:
plate

Plate(name='test_plate', size_x=127.76, size_y=85.48, size_z=14.2, location=Coordinate(000.000, 000.000, 000.000))

In [31]:

results = await pr.read_absorbance(
    plate=plate,
    wavelength=600,
    well_scan="spiral",
    flashes=25,
    shake_mode="orbital",
    shake_speed=300,
    shake_duration_s=20,
    use_new_return_type=True
)


display(pd.DataFrame(results[0]["data"]))

print(results)

TypeError: pylabrobot.plate_reading.bmg_labtech.clariostar_plus_backend.CLARIOstarPlusBackend.read_absorbance() got multiple values for keyword argument 'plate'

In [26]:
### T2: Flash counts — extremes
print("=== T2: Flash counts ===")
_t2_tests = [
    ("T2a 1 flash",    dict(flashes=1)),
    ("T2b 5 flashes",  dict(flashes=5)),
    ("T2c 20 flashes", dict(flashes=20)),
]
for label, kw in tqdm(_t2_tests, desc="T2"):
    await _abs(label, **kw)

=== T2: Flash counts ===


T2:   0%|          | 0/3 [00:00<?, ?it/s]

2026-02-26 18:29:48,093 - pylabrobot - INFO - --- T2a 1 flash ---
2026-02-26 18:29:48,187 - pylabrobot - INFO - read 53 bytes: 0200350c032504260000000004bc0000018c0100000027000000010100000000000000010000001d0001000000010000180002440d
2026-02-26 18:29:50,192 - pylabrobot - WARNING - data poll: bad frame (Response too short (0 bytes)), retrying
2026-02-26 18:29:50,256 - pylabrobot - INFO - read 24 bytes: 0200180c01b504260000d50000000000f600fee00004af0d
2026-02-26 18:29:50,258 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:29:51,302 - pylabrobot - INFO - read 24 bytes: 0200180c01a504260000fa0500000000f600fee00004c90d
2026-02-26 18:29:51,340 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f600fee000042f0d
2026-02-26 18:29:51,341 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:29:51,380 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f600fee00003530d
2026-02-26 18:29:51,418 - pylabrobot - INFO - read 24 bytes: 0200180c01

  PASS  T2a 1 flash (32.0s)


2026-02-26 18:30:22,167 - pylabrobot - WARNING - data poll: bad frame (Response too short (0 bytes)), retrying
2026-02-26 18:30:22,231 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f600fee000042f0d
2026-02-26 18:30:22,232 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:30:23,275 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f600fee00003530d
2026-02-26 18:30:23,313 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f600fee000042f0d
2026-02-26 18:30:23,315 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:30:23,353 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f600fee00003530d
2026-02-26 18:30:23,391 - pylabrobot - INFO - read 24 bytes: 0200180c013504260000d50000000000f600fee000042f0d
2026-02-26 18:30:23,391 - pylabrobot - INFO - measurement progress: 0/0
2026-02-26 18:30:23,431 - pylabrobot - INFO - read 24 bytes: 0200180c012504260000040100000400f600fee00003530d
2026-02-26 18

CancelledError: 

In [ ]:
### T3: Scan direction — all 4 corners, vertical/horizontal, uni/bidi
print("=== T3: Scan direction ===")
_t3_tests = [
    ("T3a TL vert uni (default)", dict(corner="TL", vertical=True,  unidirectional=True)),
    ("T3b TR vert uni",           dict(corner="TR", vertical=True,  unidirectional=True)),
    ("T3c BL vert uni",           dict(corner="BL", vertical=True,  unidirectional=True)),
    ("T3d BR vert uni",           dict(corner="BR", vertical=True,  unidirectional=True)),
    ("T3e TL horiz bidi",         dict(corner="TL", vertical=False, unidirectional=False)),
    ("T3f TL vert bidi",          dict(corner="TL", vertical=True,  unidirectional=False)),
    ("T3g BR horiz uni",          dict(corner="BR", vertical=False, unidirectional=True)),
]
for label, kw in tqdm(_t3_tests, desc="T3"):
    await _abs(label, **kw)

In [ ]:
### T4: Wavelengths — single, multi, UV, max count
print("=== T4: Wavelengths ===")
_t4_tests = [
    ("T4a 450nm single",          dict(wavelength=450)),
    ("T4b 260nm UV",              dict(wavelength=260)),
    ("T4c dual 450+600",          dict(wavelength=450, wavelengths=[450, 600], n_wl=2)),
    ("T4d triple 450+600+660",    dict(wavelength=450, wavelengths=[450, 600, 660], n_wl=3)),
    ("T4e 5-wavelength",          dict(wavelength=260, wavelengths=[260, 280, 450, 600, 750], n_wl=5)),
    ("T4f 8-wavelength (max)",    dict(wavelength=260,
                                       wavelengths=[260, 280, 350, 450, 530, 600, 700, 750], n_wl=8)),
]
for label, kw in tqdm(_t4_tests, desc="T4"):
    n_wl = kw.pop("n_wl", 1)
    await _abs(label, n_wl=n_wl, **kw)

In [ ]:
### T5: Partial well selection — single well, column, rows, scattered
print("=== T5: Partial wells ===")
_t5_tests = [
    ("T5a single well A1", dict(wells=[plate.get_item("A1")], n_wells=1)),
    ("T5b column 1 (8w)",  dict(wells=[plate.get_item(f"{r}1") for r in "ABCDEFGH"], n_wells=8)),
    ("T5c rows A-D (48w)", dict(wells=plate.get_items("A1:D12"), n_wells=48)),
    ("T5d scattered 3w",   dict(wells=[plate.get_item("A1"), plate.get_item("D6"),
                                       plate.get_item("H12")], n_wells=3)),
]
for label, kw in tqdm(_t5_tests, desc="T5"):
    n_wells = kw.pop("n_wells", 96)
    await _abs(label, n_wells=n_wells, **kw)

In [ ]:
### T6: Shake modes — orbital, linear, double_orbital; speed and duration
print("=== T6: Shake modes ===")
_sk = dict(well_scan="orbital", scan_diameter_mm=3, flashes=7)
_t6_tests = [
    ("T6a orbital 300rpm 5s",        dict(**_sk, shake_mode="orbital",        shake_speed_rpm=300, shake_duration_s=5,  settling_time_s=0.1)),
    ("T6b orbital 500rpm 5s",        dict(**_sk, shake_mode="orbital",        shake_speed_rpm=500, shake_duration_s=5,  settling_time_s=0.1)),
    ("T6c orbital 300rpm 10s",       dict(**_sk, shake_mode="orbital",        shake_speed_rpm=300, shake_duration_s=10, settling_time_s=0.1)),
    ("T6d linear 300rpm 5s",         dict(**_sk, shake_mode="linear",         shake_speed_rpm=300, shake_duration_s=5,  settling_time_s=0.1)),
    ("T6e double_orbital 300rpm 5s", dict(**_sk, shake_mode="double_orbital", shake_speed_rpm=300, shake_duration_s=5,  settling_time_s=0.1)),
]
for label, kw in tqdm(_t6_tests, desc="T6"):
    await _abs(label, **kw)

In [ ]:
### T7: Settling time
print("=== T7: Settling time ===")
_st = dict(well_scan="orbital", scan_diameter_mm=3, flashes=7,
           shake_mode="orbital", shake_speed_rpm=300, shake_duration_s=5)
_t7_tests = [
    ("T7a settle 0s",   dict(**_st, settling_time_s=0)),
    ("T7b settle 0.1s", dict(**_st, settling_time_s=0.1)),
    ("T7c settle 0.5s", dict(**_st, settling_time_s=0.5)),
]
for label, kw in tqdm(_t7_tests, desc="T7"):
    await _abs(label, **kw)

In [ ]:
### T8: Report modes — OD, transmittance, raw
print("=== T8: Report modes ===")
_t8_tests = [
    ("T8a optical_density", dict(report="optical_density")),
    ("T8b transmittance",   dict(report="transmittance")),
    ("T8c raw",             dict(report="raw", expect_cal=True)),
]
for label, kw in tqdm(_t8_tests, desc="T8"):
    expect_cal = kw.pop("expect_cal", False)
    await _abs(label, expect_cal=expect_cal, **kw)

In [ ]:
### T9: Combinations — cross-feature interactions
print("=== T9: Combinations ===")
_t9_tests = [
    ("T9a orbital + dual wl",  dict(wavelength=450, wavelengths=[450, 600], n_wl=2,
                                    well_scan="orbital", scan_diameter_mm=3, flashes=7)),
    ("T9b shake + dual wl",    dict(wavelength=450, wavelengths=[450, 600], n_wl=2,
                                    well_scan="orbital", scan_diameter_mm=3, flashes=7,
                                    shake_mode="orbital", shake_speed_rpm=300, shake_duration_s=5, settling_time_s=0.1)),
    ("T9c shake + partial",    dict(wells=[plate.get_item(f"{r}1") for r in "ABCDEFGH"], n_wells=8,
                                    well_scan="orbital", scan_diameter_mm=3, flashes=7,
                                    shake_mode="orbital", shake_speed_rpm=300, shake_duration_s=5, settling_time_s=0.1)),
    ("T9d spiral + dual wl",   dict(wavelength=450, wavelengths=[450, 600], n_wl=2,
                                    well_scan="spiral", scan_diameter_mm=3, flashes=15)),
    ("T9e orbital + single A1", dict(wells=[plate.get_item("A1")], n_wells=1,
                                     well_scan="orbital", scan_diameter_mm=3, flashes=7)),
    ("T9f dual wl + partial",  dict(wavelength=450, wavelengths=[450, 600], n_wl=2,
                                    wells=[plate.get_item(f"{r}1") for r in "ABCDEFGH"], n_wells=8)),
    ("T9g dual wl + settle",   dict(wavelength=450, wavelengths=[450, 600], n_wl=2,
                                    well_scan="orbital", scan_diameter_mm=3, flashes=7,
                                    shake_mode="orbital", shake_speed_rpm=300, shake_duration_s=3, settling_time_s=0.5)),
]
for label, kw in tqdm(_t9_tests, desc="T9"):
    n_wl = kw.pop("n_wl", 1)
    n_wells = kw.pop("n_wells", 96)
    await _abs(label, n_wl=n_wl, n_wells=n_wells, **kw)

In [ ]:
### T10: Non-blocking round-trip
print("=== T10: Non-blocking ===")
await pr.read_absorbance(wavelength=600, wait=False, use_new_return_type=True)
status = await clariostar_plus_backend.request_machine_status()
while status["busy"]:
    await asyncio.sleep(1)
    status = await clariostar_plus_backend.request_machine_status()
t0 = time.monotonic()
results = await clariostar_plus_backend.request_absorbance_results(
    plate, plate.get_all_items(), [600])
dt = time.monotonic() - t0
passed = _v(results, "T10a non-blocking round-trip")
_all_results["T10a non-blocking round-trip"] = {
    "passed": passed,
    "duration_s": round(dt, 2),
    "n_wl": 1,
    "n_wells": 96,
    "params": {"wavelength": 600, "wait": False},
    "results": results,
}

### Save all test data
_n_pass = sum(1 for v in _all_results.values() if v["passed"])
_n_total = len(_all_results)
print(f"\n=== All hardware validation tests complete: {_n_pass}/{_n_total} PASS ===")

# Save results to a timestamped JSON file for future comparison.
# Well objects are not JSON-serializable, so we filter them from params.
def _serializable(obj):
    """Convert non-serializable objects to strings for JSON output."""
    if hasattr(obj, "name"):
        return obj.name
    return str(obj)

_ts = datetime.now().strftime("%Y%m%d_%H%M%S")
_save_path = f"clariostar_test_data_{_ts}.json"
_save_data = {
    "run_start": _test_run_start,
    "run_end": datetime.now(timezone.utc).isoformat(),
    "serial_number": clariostar_plus_backend.configuration.get("serial_number", ""),
    "firmware_version": clariostar_plus_backend.configuration.get("firmware_version", ""),
    "n_pass": _n_pass,
    "n_total": _n_total,
    "tests": {},
}
for label, entry in _all_results.items():
    # Make params serializable (remove Well objects, keep primitives)
    safe_params = {}
    for k, v in entry["params"].items():
        if k == "wells":
            safe_params[k] = [w.name if hasattr(w, "name") else str(w) for w in v]
        elif k == "wavelengths":
            safe_params[k] = v
        else:
            safe_params[k] = v
    _save_data["tests"][label] = {
        "passed": entry["passed"],
        "duration_s": entry["duration_s"],
        "n_wl": entry["n_wl"],
        "n_wells": entry["n_wells"],
        "params": safe_params,
        "results": entry["results"],
    }
with open(_save_path, "w") as f:
    _json.dump(_save_data, f, indent=2, default=_serializable)
print(f"Test data saved to: {_save_path}")

---
## Planned Features

The sections below cover measurement modes that are not yet implemented.
Code cells are commented out and will be uncommented as each feature lands.

### Fluorescence

Basic, custom gain/bandwidth, bottom-optic.

In [ ]:
# results = await pr.read_fluorescence(
#     excitation_wavelength=485,
#     emission_wavelength=528,
#     focal_height=8.5,
# )
#
# print(f"GFP fluorescence, well A1: {results[0]['data'][0][0]}")

In [ ]:
# results = await pr.read_fluorescence(
#     excitation_wavelength=485,
#     emission_wavelength=528,
#     focal_height=8.5,
#     flashes=50,
# )

In [ ]:
# Bottom-optic fluorescence (e.g. for cell-based assays)
# results = await pr.read_fluorescence(
#     excitation_wavelength=544,
#     emission_wavelength=590,
#     focal_height=4.5,
# )

### Luminescence

Basic luminescence, partial well selection.

In [ ]:
# results = await pr.read_luminescence(
#     focal_height=13.0,
# )
#
# print(f"Temperature: {results[0]['temperature']:.1f} °C")
# print(f"Well A1 RLU: {results[0]['data'][0][0]}")

In [ ]:
# selected_wells = [plate.get_item("A1"), plate.get_item("D6"), plate.get_item("H12")]
#
# results = await pr.read_luminescence(
#     focal_height=13.0,
#     wells=selected_wells,
# )

In [ ]:
# row_A = [plate.get_item(f"A{col}") for col in range(1, 13)]
#
# results = await pr.read_fluorescence(
#     excitation_wavelength=544,
#     emission_wavelength=590,
#     focal_height=6.0,
#     wells=row_A,
#     shake_mode="orbital",
#     shake_speed_rpm=300,
#     shake_duration_s=3,
#     settling_time_s=0.1,
#     corner="BR",
# )

---
## Reference: How Absorbance Calculation Works

The machine does not measure absorbance directly. It measures **raw detector counts**
and the backend converts them to transmittance and then to OD.

**OD formula:**

```
T = (sample / c_hi) × (r_hi / ref)
OD = -log10(T)
```

Where:
- `sample` = per-well sample detector count
- `ref` = per-well reference detector count
- `c_hi` = chromatic calibration value for this wavelength
- `r_hi` = reference calibration value

**Multi-wavelength data layout:**

The firmware response contains data as groups of per-well u32 values followed by
calibration pairs. The number of groups scales with wavelength count:

| Wavelengths | Groups | Calibration pairs | Layout |
|:-----------:|:------:|:-----------------:|--------|
| 1 | 4 | 4 | WL1, chrom2, chrom3, reference |
| 2 | 5 | 5 | WL1, WL2, chrom2, chrom3, reference |
| 3 | 6 | 6 | WL1, WL2, WL3, chrom2, chrom3, reference |
| W | W+3 | W+3 | WL1…WLW, chrom2, chrom3, reference |

Each wavelength's OD is computed using **its own calibration pair** (WL1 → cal\[0\],
WL2 → cal\[1\], etc.) and the shared reference detector (last group, last cal pair).
The backend detects the number of groups dynamically from the payload size, so it
handles any wavelength count without configuration.

See `DESIGN.md` in `pylabrobot/plate_reading/bmg_labtech/` for the full protocol reference.

---
## Closing Connection

In [ ]:
pr.unassign_child_resource(plate)

In [ ]:
await pr.stop()

This closes the FTDI connection. After calling `stop()`, you must call `setup()` again before using the plate reader.